In [28]:
from pathlib import Path
from label_studio_sdk.client import LabelStudio
from fishsense_api_sdk.client import Client
from label_studio_sdk.core import ApiError
import pandas as pd
from tqdm.notebook import tqdm
import pickle
from tqdm.asyncio import tqdm_asyncio
import json

In [3]:
URL = "http://localhost:8000"

In [4]:
LABEL_STUDIO_PROJECT_IDS = [45, 44]

LABEL_STUDIO_PROJECT_IDS

[45, 44]

In [5]:
label_studio_api_key = Path("..") / ".label_studio_api_key"

label_studio_api_key.exists()

True

In [6]:
label_studio_ids_to_fix = pd.read_csv(Path("./data-1763862357582.csv"))["label_studio_task_id"].tolist()

len(label_studio_ids_to_fix), label_studio_ids_to_fix[:5]

(22081, [148410, 165054, 148487, 165055, 148523])

In [7]:
ls = LabelStudio(base_url=f"https://labeler.e4e.ucsd.edu", api_key=label_studio_api_key.read_text().strip())

In [8]:
# tasks = []

# for idx in tqdm(label_studio_ids_to_fix):
#     try:
#         task = ls.tasks.get(idx)
#     except ApiError as e:
#         continue

#     tasks.append(task)

# len(tasks), tasks[0]

In [9]:
# pickle.dump(tasks, open(Path("./fixed_headtail_tasks.pkl"), "wb"))

In [10]:
tasks = pickle.load(open(Path("./fixed_headtail_tasks.pkl"), "rb"))

len(tasks), tasks[0]

(16473,
 LseTask(agreement=None, agreement_selected=None, annotations=[{'id': 118444, 'result': [], 'created_username': ' jen.loch@reef.org, 26', 'created_ago': '1\xa0month', 'completed_by': {'id': 26, 'first_name': '', 'last_name': '', 'avatar': None, 'email': 'jen.loch@reef.org', 'initials': 'je'}, 'was_cancelled': False, 'ground_truth': False, 'created_at': '2025-10-22T14:38:47.444237Z', 'updated_at': '2025-10-22T14:38:47.444247Z', 'draft_created_at': '2025-10-22T14:38:45.262075Z', 'lead_time': 129.416, 'import_id': None, 'last_action': None, 'bulk_created': False, 'task': 165054, 'project': 45, 'updated_by': 26, 'parent_prediction': None, 'parent_annotation': None, 'last_created_by': None}], annotations_ids='118444', annotations_results='', annotators=[26], annotators_count=None, avg_lead_time=129.416, cancelled_annotations=0, comment_authors=[], comment_authors_count=None, comment_count=0, comments=None, completed_at=datetime.datetime(2025, 10, 22, 14, 38, 47, 444237, tzinfo=datet

In [11]:
image_checksums = [t.data["img"].split("/")[-1] for t in tasks]

image_checksums[:5]

['5f14f3565262881bf1f6b6e0caeb5f7c',
 '9df75b3bc37530eccb7643e5a3a6b06a',
 '76c358c78b0e485857b5730b0768428c',
 '9b4778d65008ec1f4d54f227e95a2e3e',
 '2ccbcfe2e7318071296837fefdfc0b36']

In [ ]:
async with Client(URL) as client:
    images = await tqdm_asyncio.gather(
        *[client.images.get(checksum=checksum) for checksum in image_checksums]
    )

len(images), images[0]

100%|██████████| 16473/16473 [04:52<00:00, 56.39it/s]


16473

In [26]:
async with Client(URL) as client:
    headtail_labels = await tqdm_asyncio.gather(
        *[client.labels.get_headtail_label(image_id=image.id) for image in images]
    )
    headtail_labels = [l for l in headtail_labels if l is not None]

len(headtail_labels), headtail_labels[0]

100%|██████████| 16473/16473 [05:55<00:00, 46.34it/s]


(16472,
 HeadTailLabel(id=2, label_studio_task_id=165054, label_studio_project_id=None, head_x=None, head_y=None, tail_x=None, tail_y=None, updated_at=None, completed=False, label_studio_json=None, image_id=79158, user_id=None))

In [14]:
tasks_by_id = {t.id: t for t in tasks}

tasks_by_id

{165054: LseTask(agreement=None, agreement_selected=None, annotations=[{'id': 118444, 'result': [], 'created_username': ' jen.loch@reef.org, 26', 'created_ago': '1\xa0month', 'completed_by': {'id': 26, 'first_name': '', 'last_name': '', 'avatar': None, 'email': 'jen.loch@reef.org', 'initials': 'je'}, 'was_cancelled': False, 'ground_truth': False, 'created_at': '2025-10-22T14:38:47.444237Z', 'updated_at': '2025-10-22T14:38:47.444247Z', 'draft_created_at': '2025-10-22T14:38:45.262075Z', 'lead_time': 129.416, 'import_id': None, 'last_action': None, 'bulk_created': False, 'task': 165054, 'project': 45, 'updated_by': 26, 'parent_prediction': None, 'parent_annotation': None, 'last_created_by': None}], annotations_ids='118444', annotations_results='', annotators=[26], annotators_count=None, avg_lead_time=129.416, cancelled_annotations=0, comment_authors=[], comment_authors_count=None, comment_count=0, comments=None, completed_at=datetime.datetime(2025, 10, 22, 14, 38, 47, 444237, tzinfo=datet

In [31]:
label_coroutines = []

async with Client(URL) as client:
    for label in headtail_labels:
        task = tasks_by_id[label.label_studio_task_id]

        label.label_studio_json = json.loads(task.json())

        label_coroutines.append(client.labels.put_headtail_label(label.image_id, label))

    await tqdm_asyncio.gather(*label_coroutines)
    

/home/chris/Repos/school/e4e/fishsense/fishsense-data-processing-workflow-worker/.venv/lib/python3.13/site-packages/label_studio_sdk/core/pydantic_utilities.py:88: UserWarning: Pydantic serializer warnings:
  PydanticSerializationUnexpectedValue(Expected `str` - serialized value may not be as expected [field_name='annotations', input_value=[{'id': 118444, 'result':...last_created_by': None}], input_type=list])
  serialized = handler(self)
/home/chris/Repos/school/e4e/fishsense/fishsense-data-processing-workflow-worker/.venv/lib/python3.13/site-packages/label_studio_sdk/core/pydantic_utilities.py:88: UserWarning: Pydantic serializer warnings:
  PydanticSerializationUnexpectedValue(Expected `str` - serialized value may not be as expected [field_name='annotations', input_value=[{'id': 125988, 'result':...last_created_by': None}], input_type=list])
  serialized = handler(self)
/home/chris/Repos/school/e4e/fishsense/fishsense-data-processing-workflow-worker/.venv/lib/python3.13/site-package